<a href="https://colab.research.google.com/github/vat99/makemore/blob/main/HW_1_Language_Modeling_Problem.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Project 1: Language Modeling

In this project, you will implement several different types of language models for text.  We'll start with n-gram models, then move on to neural n-gram and LSTM language models.

**Warning: Do not start this project the day before it is due!**
Some parts require 20 minutes or more to run, so debugging and tuning can take a significant amount of time.

Our dataset for this project will be the WikiText2 language modeling dataset.  We provide some of the basic preprocessing, such as tokenization and rare word filtering (using the `<unk>` token).
Therefore, we can assume that all word types in the val/test set appear at least once in the training set.

In [1]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 471.6/471.6 kB 9.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 9.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 40.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 16.5 MB/s eta 0:00:00
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pyarrow<15.0.0a0,>=14.0.1, but you have pyarrow 17.0.0 which is incompatible.


In [2]:
# This block handles some imports and defines some constants.
# You shouldn't need to edit this, but if you want to
# import other standard python packages, that is fine.

# imports
from collections import Counter, defaultdict
import copy
import numpy as np
import math
import tqdm
import random
import pdb
from typing import List, Optional, Tuple, Union

from datasets import load_dataset
import torch
from torch import nn
import torch.nn.functional as F

# Some constants
UNK_TOK = "<unk>"
PAD_TOK = "<pad>"
EOS_TOK = "<eos>"

In [3]:
# This block defines the Vocabulary class we need later.
# You shouldn't need to edit this.

class Vocab:
    def __init__(self, train_text: List[str], min_freq=0):
        """
        We collect counts from train_text.
        train_text: a list of tokens.
        min_freq: if a token appears strictly less than this, it will not be
            added to vocab.
        """
        special_tokens = [UNK_TOK, PAD_TOK, EOS_TOK]

        counter = Counter(train_text)
        # Note that the order is fixed as long as the training text is the same.
        # it's sorted by frequency.
        all_tokens = [
            t for t, c in counter.most_common()
            if c >= min_freq and t not in special_tokens
        ]

        self.all_tokens = special_tokens + all_tokens
        self.str_to_id = {s: i for i, s in enumerate(self.all_tokens)}

        self.unk_tok = UNK_TOK
        self.pad_tok = PAD_TOK
        self.eos_tok = EOS_TOK

    def size(self) -> int:
        return len(self.all_tokens)


    def ids_to_strs(self, indices: List[int]) -> List[str]:
        return [self.all_tokens[ii] for ii in indices]


    def strs_to_ids(self, strings: List[str]) -> List[int]:
        return [self.str_to_id[s] for s in strings]


    def __contains__(self, token: str) -> bool:
        return token in self.str_to_id

In [4]:
# This block downloads and processes the data.
# You shouldn't need to edit this.

wikitext2_dataset = load_dataset("Salesforce/wikitext", "wikitext-2-raw-v1")
print(f"Raw train examples: {wikitext2_dataset['train']['text'][:10]}")

# just use the simplest one for now
tokenizer = lambda x: x.split()

# tokenize datatsets
def preprocess(_dataset: List[str]) -> List[str]:
    """
    Each sentence in _dataset is tokenized into a list of strings.
    _dataset: List[str]. Each string is a sentence.
    """
    ret = []
    for sent in _dataset:
        sent = sent.rstrip('\n')
        # skip empty sentences
        if not sent:
            continue
        # add EOS to the end of sentence
        ret += tokenizer(sent) + [EOS_TOK]
    return ret

tok_train_dataset = preprocess(wikitext2_dataset['train']['text'])
tok_validation_dataset = preprocess(wikitext2_dataset['validation']['text'])
tok_test_dataset = preprocess(wikitext2_dataset['test']['text'])
print(f"Dataset size (#tokens) - Train: {len(tok_train_dataset)}; Validation: {len(tok_validation_dataset)}; Test: {len(tok_test_dataset)}.")

# build vocabulary: use `min_freq` to model UNK in training
### You'll need this vocab throughout this HW.
vocab = Vocab(tok_train_dataset, min_freq=2)
print(f"Vocab size: {vocab.size()}. Examples: {vocab.ids_to_strs(list(range(20)))}")

# handle UNKs properly
def replace_unseen_with_unk(_dataset: List[str]) -> List[str]:
    """
    We replace the unseen tokens in _dataset with vocab.unk_tok.
    """
    new_data = []
    for tok in _dataset:
        if tok in vocab:
            new_data.append(tok)
        else:
            new_data.append(vocab.unk_tok)
    return new_data

### You'll need these three datasets throughout this HW.
tok_train_dataset = replace_unseen_with_unk(tok_train_dataset)
tok_validation_dataset = replace_unseen_with_unk(tok_validation_dataset)
tok_test_dataset = replace_unseen_with_unk(tok_test_dataset)
print(f"Final train examples: {tok_train_dataset[:40]}")
print(f"Final val examples: {tok_validation_dataset[:40]}")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/10.5k [00:00<?, ?B/s]

test-00000-of-00001.parquet:   0%|          | 0.00/733k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/6.36M [00:00<?, ?B/s]

validation-00000-of-00001.parquet:   0%|          | 0.00/657k [00:00<?, ?B/s]

Generating test split:   0%|          | 0/4358 [00:00<?, ? examples/s]

Generating train split:   0%|          | 0/36718 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/3760 [00:00<?, ? examples/s]

Raw train examples: ['', ' = Valkyria Chronicles III = \n', '', ' Senjō no Valkyria 3 : Unrecorded Chronicles ( Japanese : 戦場のヴァルキュリア3 , lit . Valkyria of the Battlefield 3 ) , commonly referred to as Valkyria Chronicles III outside Japan , is a tactical role @-@ playing video game developed by Sega and Media.Vision for the PlayStation Portable . Released in January 2011 in Japan , it is the third game in the Valkyria series . Employing the same fusion of tactical and real @-@ time gameplay as its predecessors , the story runs parallel to the first game and follows the " Nameless " , a penal military unit serving the nation of Gallia during the Second Europan War who perform secret black operations and are pitted against the Imperial unit " Calamaty Raven " . \n', " The game began development in 2010 , carrying over a large portion of the work done on Valkyria Chronicles II . While it retained the standard features of the series , it also underwent multiple adjustments , such as making

We've implemented a unigram model here as a demonstration.

In [ ]:
class UnigramModel:
    def __init__(self, train_text: List[str]):
        self.counts = Counter(train_text)
        self.total_count = len(train_text)

    def probability(self, word: str) -> float:
        return self.counts[word] / self.total_count

    def next_word_probabilities(self, text_prefix: List[str]) -> List[str]:
        """
        Return a list of probabilities for each word in the vocabulary.
        In unigram model, `text_prefix` doesn't matter as we are not using any
            context at all.
        """
        return [self.probability(word) for word in vocab.all_tokens]

    def perplexity(self, full_text: List[str]) -> float:
        """Return the perplexity of the model on a text as a float.

        full_text -- a list of string tokens
        """
        log_probabilities = []
        for word in full_text:
            # Note that the base of the log doesn't matter
            # as long as the log and exp use the same base.
            log_probabilities.append(math.log(self.probability(word), 2))
        return 2 ** -np.mean(log_probabilities)

unigram_demonstration_model = UnigramModel(tok_train_dataset)
print('unigram validation perplexity:',
      unigram_demonstration_model.perplexity(tok_test_dataset))

unigram validation perplexity: 1057.2131456213988


In [ ]:
def check_validity(model):
    """
    Performs several sanity checks on your model:
      1) That `next_word_probabilities` returns a valid distribution
      2) That perplexity matches a perplexity calculated from `next_word_probabilities`

    Although it is possible to calculate perplexity from `next_word_probabilities`,
      it is still good to have a separate more efficient method that only computes
      the probabilities of observed words.
    """

    log_probabilities = []
    for i in range(10):
        prefix = tok_validation_dataset[:i]
        probs = model.next_word_probabilities(prefix)
        assert min(probs) >= 0, "Negative value in next_word_probabilities"
        assert max(probs) <= 1 + 1e-8, "Value larger than 1 in next_word_probabilities"
        assert abs(sum(probs)-1) < 1e-4, "next_word_probabilities do not sum to 1"

        word_id = vocab.str_to_id[tok_validation_dataset[i]]
        selected_prob = probs[word_id]
        log_probabilities.append(math.log(selected_prob))

    perplexity = math.exp(-np.mean(log_probabilities))
    your_perplexity = model.perplexity(tok_validation_dataset[:10])
    assert abs(perplexity-your_perplexity) < 0.1, "your perplexity does not " + \
    "match the one we calculated from `next_word_probabilities`,\n" + \
    "at least one of `perplexity` or `next_word_probabilities` is incorrect.\n" + \
    f"we calcuated {perplexity} from `next_word_probabilities`,\n" + \
    f"but your perplexity function returned {your_perplexity} (on a small sample)."

In [ ]:
check_validity(unigram_demonstration_model)

To generate from a language model, we can sample one word at a time conditioning on the words we have generated so far.

In [ ]:
def generate_text(model, n=20, prefix=('<eos>', '<eos>')):
    prefix = list(prefix)
    for _ in range(n):
        probs = model.next_word_probabilities(prefix)
        word = random.choices(vocab.all_tokens, probs)[0]
        prefix.append(word)
    return ' '.join(prefix)

# unigram model does not utilize prefix
print(generate_text(unigram_demonstration_model, prefix=""))

72 000 visible pieces Nixon against a battalions April a by , by Antonio in sheet <unk> nine send coniferous


TODO: Copy the printed output to your report.

In fact there are many strategies to get better-sounding samples, such as only sampling from the top-k words or sharpening the distribution with a temperature.  You can read more about sampling from a language model in this recent paper: https://arxiv.org/pdf/1904.09751.pdf.

You will need to submit some outputs from the models you implement for us to grade.  The following function will be used to generate the required output files.

In [5]:
!wget https://cal-cs288.github.io/sp21/project_files/proj_1/eval_prefixes.txt
!wget https://cal-cs288.github.io/sp21/project_files/proj_1/eval_output_vocab.txt
!wget https://cal-cs288.github.io/sp21/project_files/proj_1/eval_prefixes_short.txt
!wget https://cal-cs288.github.io/sp21/project_files/proj_1/eval_output_vocab_short.txt

def save_truncated_distribution(model, filename, short=True):
    """Generate a file of truncated distributions.

    Probability distributions over the full vocabulary are large,
    so we will truncate the distribution to a smaller vocabulary.

    Please do not edit this function
    """
    vocab_name = 'eval_output_vocab'
    prefixes_name = 'eval_prefixes'

    if short:
      vocab_name += '_short'
      prefixes_name += '_short'

    with open(f'{vocab_name}.txt', 'r') as eval_vocab_file:
        eval_vocab = [w.strip() for w in eval_vocab_file]
    eval_vocab_ids = sorted(list(set([vocab.str_to_id[s] if s in vocab else vocab.str_to_id[vocab.unk_tok]
                      for s in eval_vocab])))

    all_selected_probabilities = []
    with open(f'{prefixes_name}.txt', 'r') as eval_prefixes_file:
        lines = eval_prefixes_file.readlines()
        for line in tqdm.notebook.tqdm(lines, leave=False):
            prefix = line.strip().split(' ')
            probs = model.next_word_probabilities(prefix)
            selected_probs = np.array([probs[i] for i in eval_vocab_ids], dtype=np.float32)
            all_selected_probabilities.append(selected_probs)

    all_selected_probabilities = np.stack(all_selected_probabilities)
    np.save(filename, all_selected_probabilities)
    print('saved', filename)

--2024-09-29 23:04:02--  https://cal-cs288.github.io/sp21/project_files/proj_1/eval_prefixes.txt
Resolving cal-cs288.github.io (cal-cs288.github.io)... 185.199.108.153, 185.199.109.153, 185.199.111.153, ...
Connecting to cal-cs288.github.io (cal-cs288.github.io)|185.199.108.153|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 519055 (507K) [text/plain]
Saving to: ‘eval_prefixes.txt’

eval_prefixes.txt   100%[===================>] 506.89K  --.-KB/s    in 0.05s   

2024-09-29 23:04:02 (10.6 MB/s) - ‘eval_prefixes.txt’ saved [519055/519055]

--2024-09-29 23:04:02--  https://cal-cs288.github.io/sp21/project_files/proj_1/eval_output_vocab.txt
Resolving cal-cs288.github.io (cal-cs288.github.io)... 185.199.108.153, 185.199.109.153, 185.199.111.153, ...
Connecting to cal-cs288.github.io (cal-cs288.github.io)|185.199.108.153|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 12497 (12K) [text/plain]
Saving to: ‘eval_output_vocab.txt’

eval_output_

In [ ]:
save_truncated_distribution(unigram_demonstration_model,
                            'unigram_demonstration_predictions.npy')

  0%|          | 0/1000 [00:00<?, ?it/s]

saved unigram_demonstration_predictions.npy


### N-gram Model

Now it's time to implement an n-gram language model.

Because not every n-gram will have been observed in training, use add-alpha smoothing to make sure no output word has probability 0.

This is an example of bigram model with smoothing:
$$P(w_2|w_1)=\frac{C(w_1,w_2)+\alpha}{C(w_1)+N\alpha}$$

where $N$ is the vocab size and $C$ is the count for the given unigram/bigram.  An alpha value around `3e-3`  should work.  Later, we'll replace this smoothing with model backoff.

One **edge case** you will need to handle is at the beginning of the text where you don't have `n-1` prior words.  You may handle this by using a uniform distribution over the vocabulary.

A properly implemented bi-gram model should get a perplexity about/below **635** on the validation set.

**Note**: Do not change the signature of the `next_word_probabilities` and `perplexity` functions.  We will use these as a common interface for all of the different model types.  Make sure these two functions call `n_gram_probability`, because later we are going to override `n_gram_probability` in a subclass.
Also, we suggest pre-computing and caching the counts $C$ when you initialize `NGramModel` for efficiency.

In [ ]:
sequences, sequences_tokenized = [], []
sequence, sequence_tokens = "", []
for i, s in enumerate(tok_train_dataset[:226]):
  token = vocab.str_to_id[s]
  print(i, s, token)
  sequence += s
  sequence_tokens.append(token)
  if s == "<eos>":
    sequences.append(sequence)
    sequences_tokenized.append(sequence_tokens)
    sequence = ""
    sequence_tokens = []
print(sequences)
print(sequences_tokenized)

print(tok_train_dataset[-1])

0 = 11
1 Valkyria 3909
2 Chronicles 4420
3 III 851
4 = 11
5 <eos> 2
6 Senjō 20629
7 no 128
8 Valkyria 3909
9 3 91
10 : 44
11 <unk> 0
12 Chronicles 4420
13 ( 24
14 Japanese 753
15 : 44
16 戦場のヴァルキュリア3 27247
17 , 4
18 lit 7037
19 . 5
20 Valkyria 3909
21 of 6
22 the 3
23 Battlefield 23381
24 3 91
25 ) 23
26 , 4
27 commonly 1905
28 referred 981
29 to 9
30 as 17
31 Valkyria 3909
32 Chronicles 4420
33 III 851
34 outside 690
35 Japan 955
36 , 4
37 is 25
38 a 10
39 tactical 7255
40 role 294
41 @-@ 15
42 playing 592
43 video 280
44 game 78
45 developed 428
46 by 22
47 Sega 14448
48 and 7
49 Media.Vision 27248
50 for 20
51 the 3
52 PlayStation 1739
53 Portable 8242
54 . 5
55 Released 10861
56 in 8
57 January 229
58 2011 339
59 in 8
60 Japan 955
61 , 4
62 it 30
63 is 25
64 the 3
65 third 255
66 game 78
67 in 8
68 the 3
69 Valkyria 3909
70 series 107
71 . 5
72 Employing 33279
73 the 3
74 same 153
75 fusion 4590
76 of 6
77 tactical 7255
78 and 7
79 real 927
80 @-@ 15
81 time 63
82 gameplay 2699
83 a

In [ ]:
sample_train_dataset = tok_train_dataset[:226]
n_gram_length = 3

sequences, sequences_tokenized = [], []
sequence, sequence_tokens = "", []
for i, s in enumerate(sample_train_dataset):
  token = vocab.str_to_id[s]
  sequence += s
  sequence_tokens.append(token)
  if s == "<eos>":
    sequences.append(sequence)
    sequences_tokenized.append(sequence_tokens)
    sequence = ""
    sequence_tokens = []

n_gram_token_sequences = []
for n, st in enumerate(sequences_tokenized[:1]):
  print(f"sequence {n}: {list(map(lambda x: vocab.all_tokens[x], st))} {st}")
  for i in range(len(st)-n_gram_length+1):
    n_gram_tokens = st[i:i+n_gram_length]
    n_gram = vocab.ids_to_strs(n_gram_tokens)
    n_gram_token_sequences.append(n_gram_tokens)
    print(n_gram_tokens, n_gram)
    assert len(n_gram_tokens) == n_gram_length
  print("\n")

sequence 0: ['=', 'Valkyria', 'Chronicles', 'III', '=', '<eos>'] [11, 3909, 4420, 851, 11, 2]
[11, 3909, 4420] ['=', 'Valkyria', 'Chronicles']
[3909, 4420, 851] ['Valkyria', 'Chronicles', 'III']
[4420, 851, 11] ['Chronicles', 'III', '=']
[851, 11, 2] ['III', '=', '<eos>']




In [ ]:
# getting the context
print(n_gram_token_sequences)
print(n_gram_token_sequences[1])
print(n_gram_token_sequences[1][:n_gram_length-1])

[[11, 3909, 4420], [3909, 4420, 851], [4420, 851, 11], [851, 11, 2]]
[3909, 4420, 851]
[3909, 4420]


In [ ]:
from collections import defaultdict

class NGramModel:
    def __init__(self, train_text: List[str], n: int = 2, alpha: float = 3e-3):
        # get counts and perform any other setup
        self.n = n
        self.smoothing = alpha

        self.n_gram_counts = defaultdict(int)
        self.n_minus_1_gram_counts = defaultdict(int)

        # get sequences from train text
        # sequences_tokenized = []
        # sequence_tokens = []
        # for _, s in enumerate(train_text):
        #   token = vocab.str_to_id[s]
        #   sequence_tokens.append(token)
        #   if s == "<eos>":
        #     sequences_tokenized.append(sequence_tokens)
        #     sequence_tokens = []

        # for st_i, st in enumerate(sequences_tokenized):
        #   #print(f"sequence {st_i}: {list(map(lambda x: vocab.all_tokens[x], st))} {st}")
        #   for i in range(len(st)-n+1):
        #     n_gram_tokens = tuple(st[i:i+n])
        #     self.n_gram_counts[n_gram_tokens] += 1
        #     self.n_minus_1_gram_counts[n_gram_tokens[:-1]] += 1
        #     assert len(n_gram_tokens) == n

        tokenized_train_text = list(map(lambda s: vocab.str_to_id[s] if vocab.__contains__(s) else vocab.str_to_id[vocab.unk_tok], train_text))
        for i in range(len(tokenized_train_text)-self.n+1):
          n_gram_tokens = tuple(tokenized_train_text[i:i+self.n])
          self.n_gram_counts[n_gram_tokens] += 1
          self.n_minus_1_gram_counts[n_gram_tokens[:-1]] += 1
          assert len(n_gram_tokens) == self.n
          assert len(n_gram_tokens[:-1]) == self.n-1

    def n_gram_probability(self, n_gram: Tuple[str, ...]):
        """Return the probability of the last word in an n-gram.

        n_gram -- a list of string tokens
        returns the conditional probability of the last token given the rest.
        """

        assert len(n_gram) == self.n, n_gram
        n_gram_count = self.n_gram_counts[n_gram]
        n_minus_1_gram_count = self.n_minus_1_gram_counts[n_gram[:-1]]
        numerator = n_gram_count + self.smoothing
        denominator = n_minus_1_gram_count + (self.smoothing * vocab.size())

        return numerator/denominator

    def next_word_probabilities(self, text_prefix: List[str]):
        """Return a list of probabilities for each word in the vocabulary."""

        # YOUR CODE HERE
        # use your function n_gram_probability
        # vocab.all_tokens contains a list of words to return probabilities for

        #print(text_prefix)
        tokenized_prefix = list(map(lambda s: vocab.str_to_id[s] if vocab.__contains__(s) else vocab.str_to_id[vocab.unk_tok], text_prefix))
        #print(tokenized_prefix)

        if len(tokenized_prefix) <= self.n-1:
          return [1.0 / vocab.size() for _ in range(vocab.size())]

        probabilities = []
        for token in vocab.strs_to_ids(vocab.all_tokens):
          context = []
          if self.n > 1:
            context = tokenized_prefix[-(self.n-1):]
          n_gram_current = tuple(context + [token])
          assert len(n_gram_current) == self.n
          probabilities.append(self.n_gram_probability(n_gram_current))

        return probabilities

    def perplexity(self, full_text: List[str]):
        """ full_text is a list of string tokens
        return perplexity as a float """

        # YOUR CODE HERE
        # use your function n_gram_probability
        # This method should differ a bit from the example unigram model because
        # the first n-1 words of full_text must be handled as a special case.
        token_count = 0
        log_prob_sum = 0
        tokenized_full_text = list(map(lambda s: vocab.str_to_id[s] if vocab.__contains__(s) else vocab.str_to_id[vocab.unk_tok], full_text))
        for i in range(len(tokenized_full_text)):
          if i <= self.n-1:
            log_prob_sum += math.log(1 / vocab.size())
          else:
            n_gram = tuple(tokenized_full_text[i-self.n+1:i+1])
            log_prob_sum += math.log(self.n_gram_probability(n_gram))
          token_count += 1

        average_log_prob = log_prob_sum / token_count
        return math.exp(-average_log_prob)


unigram_model = NGramModel(tok_train_dataset, 1)
check_validity(unigram_model)
print('unigram validation perplexity:', unigram_model.perplexity(tok_validation_dataset)) # this should be the almost the same as our unigram model perplexity above

bigram_model = NGramModel(tok_train_dataset, n=2)
check_validity(bigram_model)
print('bigram validation perplexity:', bigram_model.perplexity(tok_validation_dataset))

trigram_model = NGramModel(tok_train_dataset, n=3)
check_validity(trigram_model)
print('trigram validation perplexity:', trigram_model.perplexity(tok_validation_dataset)) # this won't do very well...

unigram validation perplexity: 1096.29446153107
bigram validation perplexity: 635.6121589105167
trigram validation perplexity: 4287.937643068801


In [ ]:
save_truncated_distribution(bigram_model, 'bigram_predictions.npy') # this might take a few minutes

  0%|          | 0/1000 [00:00<?, ?it/s]

saved bigram_predictions.npy


Please download `bigram_predictions.npy` once you finish this section so that you can submit it.

In the block below, please report your bigram validation perplexity.  (We will use this to help us calibrate our scoring on the test set.)

TODO: Report the perplexity in your report.

Bigram validation perplexity: ***fill in here***

We can also generate samples from the model to get an idea of how it is doing.

In [ ]:
print(generate_text(bigram_model))

<eos> <eos> = = = = <eos> King <unk> de Janeiro instated crucial Takashi commissions Nexon concise endurance misdemeanour Ansari Dr. Crimint


We now free up some RAM, **it is important to run the cell below, otherwise you will likely run out of RAM in the Colab runtime.**

In [ ]:
# Free up some RAM.
del bigram_model
del trigram_model

This basic model works okay for bigrams, but a better strategy (especially for higher-order models) is to use backoff.  Implement backoff with absolute discounting.
$$P\left(w_i|w_{i-n+1}^{i-1}\right)=\frac{max\left\{C(w_{i-n+1}^i)-\delta,0\right\}}{\sum_{w_i} C(w_{i-n+1}^i)} + \alpha(w_{i-n+1}^{i-1}) P(w_i|w_{i-n+2}^{i-1})$$

$$\alpha\left(w_{i-n+1}^{i-1}\right)=\frac{\delta N_{1+}(w_{i-n+1}^{i-1})}{{\sum_{w_i} C(w_{i-n+1}^i)}}$$
where $N_{1+}$ is the number of words that appear after the previous $n-1$ words (the number of times the max will select something other than 0 in the first equation).  If $\sum_{w_i} C(w_{i-n+1}^i)=0$, use the lower order model probability directly (the above equations would have a division by 0).

We found a discount $\delta$ of 0.9 to work well based on validation performance.  A trigram model with this discount value should get a validation perplexity around/below **310**.

In [ ]:
from typing import Dict

class DiscountBackoffModel(NGramModel):
    def __init__(self, train_text: List[str],
                 lower_order_model: Union[NGramModel, "DiscountBackoffModel"],
                 n: int = 2,
                 delta: float = 0.9):
        """We only use n>=2"""
        assert n >= 2, n
        super().__init__(train_text, n=n)
        self.lower_order_model = lower_order_model
        self.discount = delta

        self.n_gram_counts = self._build_n_gram_counts(train_text, n)
        self.context_gram_counts = self._build_n_gram_counts(train_text, n-1)

        # Additional counts for Kneser-Ney smoothing
        self.continuation_counts = self._build_continuation_counts()
        self.total_continuations = sum(self.continuation_counts.values())

    def _build_n_gram_counts(self, text: List[str], n: int) -> Dict[Tuple[str, ...], int]:
        counts = defaultdict(int)
        for i in range(len(text)-n+1):
            n_gram = tuple(text[i:i+n])
            counts[n_gram] += 1
        return counts

    def _build_continuation_counts(self) -> Dict[str, int]:
        continuations = defaultdict(set)
        for n_gram in self.n_gram_counts:
            context, word = n_gram[:-1], n_gram[-1]
            continuations[word].add(context)
        return {word: len(contexts) for word, contexts in continuations.items()}

    def n_gram_probability(self, n_gram: Tuple[str, ...]) -> float:
        assert len(n_gram) == self.n

        context = n_gram[:-1]
        word = n_gram[-1]

        n_gram_count = self.n_gram_counts.get(n_gram, 0)
        context_gram_count = self.context_gram_counts.get(context, 0)

        if context_gram_count == 0:
            return self.lower_order_model.n_gram_probability(n_gram[1:])

        discounted_prob = max(n_gram_count - self.discount, 0) / context_gram_count

        # Kneser-Ney probability for lower-order model
        if isinstance(self.lower_order_model, DiscountBackoffModel):
            continuation_count = self.continuation_counts.get(word, 0)
            lower_order_prob = continuation_count / self.total_continuations
        else:
            lower_order_prob = self.lower_order_model.n_gram_probability(n_gram[1:])

        distinct_continuations = len([ngram for ngram in self.n_gram_counts if ngram[:-1] == context])
        alpha = (self.discount * distinct_continuations) / context_gram_count

        return discounted_prob + alpha * lower_order_prob

# class DiscountBackoffModel(NGramModel):
#     def __init__(self, train_text: List[str],
#                  lower_order_model: Union[NGramModel, "DiscountBackoffModel"],
#                  n: int = 2,
#                  delta: float = 0.9):
#         """We only use n>=2"""
#         assert n >= 2, n
#         super().__init__(train_text, n=n)
#         self.lower_order_model = lower_order_model
#         self.discount = delta

#         # YOUR CODE HERE
#         self.n_gram_counts = self._build_n_gram_counts(train_text, n)
#         self.context_gram_counts = self._build_n_gram_counts(train_text, n-1)

#         self.n_gram_counts_updated = defaultdict(int)
#         self.context_gram_counts_updated = defaultdict(int)
#         for i in range(n - 1, len(train_text)):
#             n_gram = tuple(train_text[i - n + 1: i + 1])
#             context = n_gram[:-1]
#             self.n_gram_counts_updated[n_gram] += 1
#             self.context_gram_counts_updated[context] += 1

#     def _build_n_gram_counts(self, text: List[str], n: int) -> Dict[Tuple[str, ...], int]:
#         counts = defaultdict(int)
#         for i in range(len(text)-n+1):
#           n_gram = tuple(text[i:i+n])
#           counts[n_gram] += 1
#         return counts

#     def n_gram_probability(self, n_gram: Tuple[str, ...]) -> float:
#         assert len(n_gram) == self.n

#         # YOUR CODE HERE
#         # back off to the lower_order model with n'=n-1 using its n_gram_probability function
#         context = n_gram[:-1]
#         word = n_gram[-1]

#         n_gram_count = self.n_gram_counts.get(n_gram, 0)
#         context_gram_count = self.context_gram_counts.get(context, 0)
#         if context_gram_count == 0:
#           return self.lower_order_model.n_gram_probability(n_gram[1:])

#         discounted_prob = max(n_gram_count - self.discount, 0) / context_gram_count
#         backoff_prob = self.lower_order_model.n_gram_probability(n_gram[1:])
#         distinct_continuations = len([ngram for ngram in self.n_gram_counts if ngram[:-1] == context])
#         alpha = (self.discount * distinct_continuations) / context_gram_count
#         return discounted_prob + alpha * backoff_prob


In [ ]:
bigram_backoff_model = DiscountBackoffModel(tok_train_dataset, unigram_model, 2)

In [ ]:
sample_n_gram = list(bigram_backoff_model.n_gram_counts.keys())[1]
print(sample_n_gram)
print(bigram_backoff_model.n_gram_counts[sample_n_gram])#, bigram_backoff_model.n_gram_counts_updated[sample_n_gram])
sample_context_gram = sample_n_gram[:-1]
print(sample_context_gram)
print(bigram_backoff_model.context_gram_counts[sample_context_gram])#, bigram_backoff_model.context_gram_counts_updated[sample_context_gram])
print(len([ngram for ngram in bigram_backoff_model.n_gram_counts if ngram[:-1] == sample_context_gram]))

('Valkyria', 'Chronicles')
36
('Valkyria',)
54
10


In [ ]:
bigram_backoff_model = DiscountBackoffModel(tok_train_dataset, unigram_model, 2)
check_validity(bigram_backoff_model)
print('bigram backoff validation perplexity:', bigram_backoff_model.perplexity(tok_validation_dataset))

trigram_backoff_model = DiscountBackoffModel(tok_train_dataset, bigram_backoff_model, 3)
check_validity(trigram_backoff_model)
print('trigram backoff validation perplexity:', trigram_backoff_model.perplexity(tok_validation_dataset))

bigram backoff validation perplexity: 1096.2887206509392
trigram backoff validation perplexity: 1096.2748284683664


In [ ]:
save_truncated_distribution(trigram_backoff_model, 'trigram_pbackoff_redictions.npy') # this might take a few minutes

  0%|          | 0/1000 [00:00<?, ?it/s]

saved trigram_pbackoff_redictions.npy


TODO: Report your trigram backoff model perplexity.

Trigram backoff validation perplexity: ***fill in here***

Free up RAM.

In [ ]:
# Release models we don't need any more.
del unigram_model
del bigram_backoff_model
del trigram_backoff_model

### Neural N-gram Model

In this section, you will implement a neural version of an n-gram model.  The model will use a simple feedforward neural network that takes the previous `n-1` words and outputs a distribution over the next word.

You will use PyTorch to implement the model.  We've provided a little bit of code to help with the data loading using PyTorch's data loaders (https://pytorch.org/docs/stable/data.html)

A model with the following architecture and hyperparameters should reach a validation perplexity around/below **240**.
* embed the words with dimension 128, then flatten into a single embedding for $n-1$ words (with size $(n-1)*128$)
* run 2 hidden layers with 1024 hidden units, then project down to size 128 before the final layer (ie. 4 layers total).
* use weight tying for the embedding and final linear layer (this made a very large difference in our experiments); you can do this by creating the output layer with `nn.Linear`, then using `F.embedding` with the linear layer's `.weight` to embed the input
* rectified linear activation (ReLU) and dropout 0.1 after first 2 hidden layers. **Note: You will likely find a performance drop if you add a nonlinear activation function after the dimension reduction layer.**
* train for 10 epochs with the Adam optimizer (should take around 15-20 minutes)
* do early stopping based on validation set perplexity.


We encourage you to try other architectures and hyperparameters, and you will likely find some that work better than the ones listed above.  A proper implementation with these should be enough to receive full credit on the assignment, though.

In [ ]:
class NeuralNgramDataset(torch.utils.data.Dataset):
    def __init__(self, text_token_ids: List[int], n: int):
        self.text_token_ids = text_token_ids
        self.n = n

    def __len__(self):
        return len(self.text_token_ids)

    def __getitem__(self, i: int):
        if i < self.n - 1:
            prev_token_ids = [vocab.str_to_id[vocab.eos_tok]] * (self.n - i - 1) + \
                              self.text_token_ids[:i]
        else:
            prev_token_ids = self.text_token_ids[i - self.n + 1 : i]

        assert len(prev_token_ids) == self.n - 1, prev_token_ids

        x = torch.tensor(prev_token_ids, dtype=torch.long)
        y = torch.tensor(self.text_token_ids[i], dtype=torch.long)
        return x, y

class NeuralNGramNetwork(nn.Module):
    # a PyTorch Module that holds the neural network for your model

    def __init__(
            self, n: int,
            embed_dim: int = 128,
            hidden_dim: int = 1024,
            dropout_rate: float = 0.1
        ):
        super().__init__()
        self.n = n

        # YOUR CODE HERE
        self.embed_dim = embed_dim
        self.hidden_dim = hidden_dim

        # Embedding layer
        self.embedding = nn.Embedding(vocab.size(), embed_dim)

        # Hidden layers
        self.hidden1 = nn.Linear((n-1) * embed_dim, hidden_dim)
        self.hidden2 = nn.Linear(hidden_dim, hidden_dim)
        self.hidden3 = nn.Linear(hidden_dim, embed_dim)

        # Output layer (tied with embedding)
        self.output = nn.Linear(embed_dim, vocab.size())
        self.output.weight = self.embedding.weight

        # Dropout
        self.dropout = nn.Dropout(dropout_rate)

        # ReLU activation
        self.relu = nn.ReLU()


    def forward(self, x):
        # x is a tensor of inputs with shape (batch, n-1)
        # this function returns a tensor of log probabilities with shape (batch, vocab_size)

        # YOUR CODE HERE
        # x shape: (batch, n-1)
        embedded = self.embedding(x)  # (batch, n-1, embed_dim)
        flattened = embedded.view(embedded.size(0), -1)  # (batch, (n-1)*embed_dim)

        hidden1 = self.relu(self.hidden1(flattened))
        hidden1 = self.dropout(hidden1)

        hidden2 = self.relu(self.hidden2(hidden1))
        hidden2 = self.dropout(hidden2)

        hidden3 = self.hidden3(hidden2)  # No ReLU here as per instructions

        output = self.output(hidden3)

        return F.log_softmax(output, dim=-1)



class NeuralNGramModel:
    # a class that wraps NeuralNGramNetwork to handle training and evaluation
    # it's ok if this doesn't work for unigram modeling
    def __init__(self, n: int, device: str = "cpu", **model_configs):
        self.n = n
        self.device = device

        if "cuda" in self.device:
            assert torch.cuda.is_available(), "no GPU found, in Co4lab go to 'Edit->Notebook settings' and choose a GPU hardware accelerator"

        self.network = NeuralNGramNetwork(n, **model_configs).to(self.device)

    def train(
        self,
        n_epoch: int = 10, lr: float = 0.001, batch_size: int = 128
    ):
        train_dataset = NeuralNgramDataset(vocab.strs_to_ids(tok_train_dataset), self.n)
        train_dataloader = torch.utils.data.DataLoader(train_dataset, batch_size=batch_size, shuffle=True)

        # iterating over train_dataloader with a for loop will return a 2-tuple of batched tensors
        # the first tensor will be previous token ids with size (batch, n-1),
        # and the second will be the current token id with size (batch, )
        # you will need to move these tensors to GPU, e.g. by using the Tensor.to() function.

        # this will take some time to run; use tqdm.notebook.tqdm to get a progress bar

        # YOUR CODE HERE
        val_dataset = NeuralNgramDataset(vocab.strs_to_ids(tok_validation_dataset), self.n)
        val_dataloader = torch.utils.data.DataLoader(val_dataset, batch_size=batch_size)

        optimizer = torch.optim.Adam(self.network.parameters(), lr=lr)
        scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=1, gamma=0.1)
        criterion = nn.NLLLoss()

        best_val_perplexity = float('inf')
        best_model = None

        for epoch in tqdm.notebook.tqdm(range(n_epoch)):
            self.network.train()
            for x, y in tqdm.notebook.tqdm(train_dataloader):
                x, y = x.to(self.device), y.to(self.device)
                optimizer.zero_grad()
                output = self.network(x)
                loss = criterion(output, y)
                loss.backward()
                optimizer.step()

            val_perplexity = self.perplexity(tok_validation_dataset)
            print(f"Epoch {epoch+1}/{n_epoch}, Validation Perplexity: {val_perplexity:.2f}")

            # if val_perplexity < best_val_perplexity:
            #     best_val_perplexity = val_perplexity
            #     best_model = copy.deepcopy(self.network.state_dict())
            # else:
            #     print("Early stopping")
            #     break

        #self.network.load_state_dict(best_model)

    def next_word_probabilities(self, text_prefix: List[str]) -> List[float]:
        # YOUR CODE HERE
        # Don't forget self.network.eval().
        # You will need to convert text_prefix from strings to numbers with the `vocab.strs_to_ids` function.
        # If your `perplexity` function below is based on a NeuralNgramDataset DataLoader, you will need to use the same strategy for prefixes with less than n-1 tokens to pass the validity check.
        # The data loader appends extra "<eos>" (end of sentence) tokens to the start of the input so there are always enough to run the network
        self.network.eval()
        with torch.no_grad():
            ids = vocab.strs_to_ids(text_prefix)
            if len(ids) < self.n - 1:
                ids = [vocab.str_to_id[vocab.eos_tok]] * (self.n - 1 - len(ids)) + ids
            else:
                ids = ids[-(self.n-1):]
            x = torch.tensor(ids, dtype=torch.long).unsqueeze(0).to(self.device)
            log_probs = self.network(x)
            return torch.exp(log_probs).squeeze(0).tolist()

    def perplexity(self, text: List[str]) -> float:
        # You may want to use a DataLoader here with a NeuralNgramDataset
        # Don't forget self.network.eval()

        # YOUR CODE HERE
        self.network.eval()
        dataset = NeuralNgramDataset(vocab.strs_to_ids(text), self.n)
        dataloader = torch.utils.data.DataLoader(dataset, batch_size=128)

        total_loss = 0
        total_tokens = 0

        with torch.no_grad():
            for x, y in dataloader:
                x, y = x.to(self.device), y.to(self.device)
                log_probs = self.network(x)
                total_loss += F.nll_loss(log_probs, y, reduction='sum').item()
                total_tokens += y.numel()

        return torch.exp(torch.tensor(total_loss / total_tokens)).item()

In [ ]:
# it's probabily better to first debug with cpu so you don't waste the limited GPU time.
# then you use device="cuda" to train on GPU.
neural_trigram_model = NeuralNGramModel(3, device="cuda")
check_validity(neural_trigram_model)
neural_trigram_model.train(lr=5e-4)
print('neural trigram validation perplexity:', neural_trigram_model.perplexity(tok_validation_dataset))

  0%|          | 0/10 [00:00<?, ?it/s]

  0%|          | 0/16217 [00:00<?, ?it/s]

Epoch 1/10, Validation Perplexity: 449.42


  0%|          | 0/16217 [00:00<?, ?it/s]

Epoch 2/10, Validation Perplexity: 378.88


...

Epoch 8/10, Validation Perplexity: 305.97


  0%|          | 0/16217 [00:00<?, ?it/s]

Epoch 9/10, Validation Perplexity: 305.55


  0%|          | 0/16217 [00:00<?, ?it/s]

Epoch 10/10, Validation Perplexity: 301.97
neural trigram validation perplexity: 301.97100830078125


In [ ]:
save_truncated_distribution(neural_trigram_model, 'neural_trigram_predictions.npy', short=False)

  0%|          | 0/5000 [00:00<?, ?it/s]

saved neural_trigram_predictions.npy


TODO: Fill in your neural trigram perplexity in the report.

<!-- Do not remove this comment, it is used by the autograder: RqYJKsoTS6 -->

Neural trigram validation perplexity: ***fill in here***

Free up RAM.

In [ ]:
# Delete model we don't need.
del neural_trigram_model

### LSTM Model

For this stage of the project, you will implement an LSTM language model.

For recurrent language modeling, the data batching strategy is a bit different from what is used in some other tasks.  Sentences are concatenated together so that one sentence starts right after the other, and an unfinished sentence will be continued in the next batch.
To properly deal with this input format, you should **save the last state of the LSTM from a batch to feed in as the first state of the next batch**.  When you save state across different batches, you should call `.detach()` on the state tensors before the next batch to tell PyTorch not to backpropagate gradients through the state into the batch you have already finished (which will cause a runtime error).

We expect your model to reach a validation perplexity around/below **214**.
The following architecture and hyperparameters should be sufficient to get there.
* 3 LSTM layers with 512 units
* dropout of 0.5 after each LSTM layer
* instead of projecting directly from the last LSTM output to the vocabulary size for softmax, project down to a smaller size first (e.g. 512->128->vocab_size). **NOTE: You may find that adding nonlinearities between these layers can hurt performance, try without first.**
* use the same weights for the embedding layer and the pre-softmax layer; dimension 128
* train with Adam (using default learning rates) for at least 20 epochs


In [6]:
# ref: https://github.com/pytorch/text/blob/0.5.0/torchtext/data/iterator.py#L173

class LstmDataIterator:
    def __init__(self, dataset: List[int], batch_size: int = 64, seq_len: int = 32, device: str = "cpu"):
        self.batch_size = batch_size
        self.seq_len = seq_len
        self.device = device

        # pad the dataset so that it is divisible by batch_size
        dataset = dataset + [vocab.str_to_id[vocab.pad_tok]] * (math.ceil(len(dataset) / batch_size) * batch_size - len(dataset))

        self.n_samples = math.ceil(
            (len(dataset) // batch_size - 1) / seq_len
        )

        dataset = torch.tensor(dataset, dtype=torch.long)
        self.dataset = dataset.view(batch_size, -1).t().contiguous()

    def __len__(self):
        return self.n_samples

    def __getitem__(self, i: int):
        start = i * self.seq_len
        end = min(start + self.seq_len, self.dataset.shape[0] - 1)

        inputs = self.dataset[start : end]
        outputs = self.dataset[start + 1 : end + 1]
        assert inputs.shape == outputs.shape, f"{i}: {inputs.shape} {outputs.shape}"
        # (seq_len, batch_size)
        return inputs.to(self.device), outputs.to(self.device)

In [48]:
import torch
from torch import nn
import torch.nn.functional as F

class LSTMNetwork(nn.Module):
    # a PyTorch Module that holds the neural network for your model

    def __init__(self, embed_dim: int = 128, n_layer: int = 3, hidden_dim: int = 512, dropout_rate: float = 0.5, embedding_type: str = "default"):
        super().__init__()

        # YOUR CODE HERE

        self.vocab_size = vocab.size()
        self.embed_dim = embed_dim
        self.hidden_dim = hidden_dim
        self.n_layer = n_layer

        # Embedding layer
        self.embedding = nn.Embedding(self.vocab_size, embed_dim)
        if embedding_type == "kaiming_normal":
          torch.nn.init.kaiming_normal_(self.embedding.weight)
        elif embedding_type == "xavier_normal":
          torch.nn.init.xavier_normal_(self.embedding.weight)

        # LSTM layers
        self.lstm = nn.LSTM(embed_dim, hidden_dim, n_layer, dropout=dropout_rate)

        # Output layers
        self.fc1 = nn.Linear(hidden_dim, embed_dim)
        self.fc2 = nn.Linear(embed_dim, self.vocab_size)

        # Tie weights
        self.fc2.weight = self.embedding.weight

    def forward(self, x: torch.Tensor, state: Optional[Tuple[torch.Tensor, torch.Tensor]]=None):
        """Compute the output of the network.

        Note: In the Pytorch LSTM tutorial, the state variable is named "hidden":
        https://pytorch.org/tutorials/beginner/nlp/sequence_models_tutorial.html

        The torch.nn.LSTM documentation is quite helpful:
        https://pytorch.org/docs/stable/generated/torch.nn.LSTM.html

        x - a tensor of int64 inputs with shape (seq_len, batch)
        state - a tuple of two tensors with shape (num_layers, batch, hidden_size)
                representing the hidden state and cell state of the of the LSTM.
        returns a tuple with two elements:
          - a tensor of log probabilities with shape (seq_len, batch, vocab_size)
          - a state tuple returned by applying the LSTM.
        """

        # Note that the nn.LSTM module expects inputs with the sequence
        # dimension before the batch by default.
        # In this case the dimensions are already in the right order,
        # but watch out for this since sometimes people put the batch first

        # YOUR CODE HERE
        # Embed the input
        embedded = self.embedding(x)

        # Pass through LSTM
        output, state = self.lstm(embedded, state)

        # Project down to embed_dim
        output = self.fc1(output)

        # Project to vocab_size
        logits = self.fc2(output)

        # Compute log probabilities
        log_probs = F.log_softmax(logits, dim=-1)

        return log_probs, state


class LSTMModel:
    "A class that wraps LSTMNetwork to handle training and evaluation."

    def __init__(self, device: str = "cpu", model: str = "default", **model_configs):
        self.device = device
        if "cuda" in self.device:
            assert torch.cuda.is_available(), "no GPU found, in Colab go to 'Edit->Notebook settings' and choose a GPU hardware accelerator"

        self.params = model_configs
        self.model_name = model
        if model == "regularized_full":
          self.network = RegularizedLSTM(**model_configs).to(self.device)
        else:
          self.network = LSTMNetwork(**model_configs).to(self.device)

    def train(
        self,
        n_epoch: int = 20, lr: float = 1e-3, batch_size: int = 64, seq_len: int = 32, patience: int = 3,
    ):
        # You can fetch the data by
        #     inputs, targets = train_data_iter[i]
        #train_data_iter = LstmDataIterator(vocab.strs_to_ids(tok_train_dataset), batch_size, seq_len, self.device)

        # The initial state passed into the LSTM should be set to zero.
        # Also note that, we don't need to compute loss on <PAD>. You can achieve
        #   this by `ignore_index=index of <PAD>` when using NLLLoss.

        # YOUR CODE HERE
        train_data_iter = LstmDataIterator(vocab.strs_to_ids(tok_train_dataset), batch_size, seq_len, self.device)

        optimizer = torch.optim.Adam(self.network.parameters(), lr=lr)
        criterion = torch.nn.NLLLoss(ignore_index=vocab.str_to_id[vocab.pad_tok])


        #best_params = {}
        #best_model = None
        #scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=2, gamma=0.9)
        WARMUP_EPOCHS=5
        WARMUP_STEPS=WARMUP_EPOCHS*len(train_data_iter)
        NORMAL_STEPS=(20)*len(train_data_iter)
        # Warmup scheduler
        #warmup_scheduler = torch.optim.lr_scheduler.LinearLR(optimizer, start_factor=lr, total_iters=WARMUP_STEPS)
        # Decay scheduler
        #decay_scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=NORMAL_STEPS,)

        # Combine schedulers
        # scheduler = torch.optim.lr_scheduler.SequentialLR(optimizer,
        #                  schedulers=[warmup_scheduler, decay_scheduler],
        #                  milestones=[WARMUP_STEPS])
        #scheduler = torch.optim.lr_scheduler.OneCycleLR(optimizer, max_lr=lr, steps_per_epoch=len(train_data_iter), epochs=20)
        #scheduler = torch.optim.lr_scheduler.ExponentialLR(optimizer, gamma=0.95)

        best_perplex = float('inf')
        patience_count = 0
        for epoch in tqdm.notebook.tqdm(range(n_epoch)):
            total_loss = 0
            state = None

            for i in tqdm.notebook.tqdm(range(len(train_data_iter))):
                inputs, targets = train_data_iter[i]

                if state is not None:
                    state = (state[0].detach(), state[1].detach())

                optimizer.zero_grad()
                log_probs, state = self.network(inputs, state)
                loss = criterion(log_probs.view(-1, vocab.size()), targets.view(-1))
                loss.backward()
                optimizer.step()

                total_loss += loss.item()

            #scheduler.step()

            # Print learning rate for this epoch
            #print(f"Epoch {epoch+1}, LR: {scheduler.get_last_lr()[0]}")

            print(f"Epoch {epoch+1}/{n_epoch}, Loss: {total_loss/len(train_data_iter):.4f}")
            val_perplex = self.dataset_perplexity(tok_validation_dataset)
            print('lstm validation perplexity:', val_perplex)
            print(f"lstm validation loss: {math.log(val_perplex)}")

            # early stopping
            if val_perplex < best_perplex:
              best_perplex = val_perplex
              regularizations_names = '-'.join(self.params['regularizations']) if 'regularizations' in self.params else "no_regularizations"
              save_truncated_distribution(self, f"lstm_{self.model_name}_{regularizations_names}_predictions_updated_{self.params}.npy", short=False)
            elif patience_count < patience:
              patience_count += 1
            else:
              break

    def next_word_probabilities(self, text_prefix: List[str]):
        "Return a list of probabilities for each word in the vocabulary."
        """
        For now, we assume it's not gonna be longer than training seq_len, so
          you can all the network only once.
        """

        # (seq, bsz=1)
        ids_prefix = torch.tensor(vocab.strs_to_ids(text_prefix), dtype=torch.long, device=self.device).view(-1, 1)

        # YOUR CODE HERE
        with torch.no_grad():
            log_probs, _ = self.network(ids_prefix)
            probs = torch.exp(log_probs[-1, 0])

        return probs.tolist()


    def dataset_perplexity(self, dataset: List[str], batch_size: int = 64, seq_len: int = 32):
        "Return perplexity as a float."
        # Your code should be very similar to next_word_probabilities, but
        # run in a loop over batches. Use torch.no_grad() for extra speed.

        data_iterator = LstmDataIterator(vocab.strs_to_ids(dataset), batch_size, seq_len, self.device)
        # YOUR CODE HERE
        total_loss = 0
        total_tokens = 0

        with torch.no_grad():
            state = None
            for i in range(len(data_iterator)):
                inputs, targets = data_iterator[i]

                if state is not None:
                    state = (state[0].detach(), state[1].detach())

                log_probs, state = self.network(inputs, state)
                loss = F.nll_loss(log_probs.view(-1, vocab.size()), targets.view(-1),
                                  ignore_index=vocab.str_to_id[vocab.pad_tok], reduction='sum')

                total_loss += loss.item()
                total_tokens += (targets != vocab.str_to_id[vocab.pad_tok]).sum().item()

        perplexity = math.exp(total_loss / total_tokens)
        return perplexity

In [8]:
lstm_model = LSTMModel(device="cuda")
lstm_model.train()

print('lstm validation perplexity:', lstm_model.dataset_perplexity(tok_validation_dataset))

  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 1/20, Loss: 6.9877
lstm validation perplexity: 493.8419265757367
lstm validation loss: 6.202215479292466


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 2/20, Loss: 6.1836
lstm validation perplexity: 365.52338156438117
lstm validation loss: 5.901330248592123


...

Epoch 18/20, Loss: 4.5250
lstm validation perplexity: 170.9048083473437
lstm validation loss: 5.141106725169541


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 19/20, Loss: 4.4875
lstm validation perplexity: 172.17597430198282
lstm validation loss: 5.148517060203674


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 20/20, Loss: 4.4525
lstm validation perplexity: 171.3723726723221
lstm validation loss: 5.143838806895942
lstm validation perplexity: 171.6078885812351


In [9]:
save_truncated_distribution(lstm_model, 'lstm_predictions.npy', short=False)

  0%|          | 0/5000 [00:00<?, ?it/s]

saved lstm_predictions.npy


TODO: Report your LSTM perplexity.

LSTM validation perplexity: ***fill in here***

# Experimentation: 1-Page Report

Now it's time for you to experiment.  Try to reach a validation perplexity below 120. You may either modify the LSTM class above, or copy it down to the code cell below and modify it there. Just **be sure to run code cell below to generate results with your improved LSTM**.  

It is okay if the bulk of your improvements are due to hyperparameter tuning (such as changing number or sizes of layers), but implement at least one more substantial change to the model.  Here are some ideas (several of which come from https://arxiv.org/pdf/1708.02182.pdf):
* activation regularization - add a l2 regularization penalty on the activation of the LSTM output (standard l2 regularization is on the weights)
* weight-drop regularization - apply dropout to the weight matrices instead of activations
* learning rate scheduling - decrease the learning rate during training
* embedding dropout - zero out the entire embedding for a random set of words in the embedding matrix
* ensembling - average the predictions of several models trained with different initialization random seeds
* temporal activation regularization - add l2 regularization on the difference between the LSTM output activations at adjacent timesteps

You may notice that most of these suggestions are regularization techniques.  This dataset is considered fairly small, so regularization is one of the best ways to improve performance.

TODO: In the report, submit a write-up describing the extensions and/or modifications that you tried.  Your description should be **1-page maximum** in length.
For full credit, your write-up should include:
1.   A concise and precise description of the extension that you tried.
2.   A motivation for why you believed this approach might improve your model.
3.   A discussion of whether the extension was effective and/or an analysis of the results.  This will generally involve some combination of tables, learning curves, etc.
4.   A bottom-line summary of your results comparing validation perplexities of your improvement to the original LSTM.


Run the cell below in order to train your improved LSTM and evaluate it.  

In [ ]:
# testing both initilaization methods against default
lstm_model_init_kaiming = LSTMModel(device="cuda", embedding_type="kaiming_normal")
lstm_model_init_kaiming.train()

print('lstm init validation perplexity kaiming_normal:', lstm_model_init_kaiming.dataset_perplexity(tok_validation_dataset))

lstm_model_init_xavier = LSTMModel(device="cuda", embedding_type="xavier_normal")
lstm_model_init_xavier.train()

print('lstm init validation perplexity xavier_normal:', lstm_model_init_xavier.dataset_perplexity(tok_validation_dataset))
#save_truncated_distribution(lstm_model_init, 'lstm_predictions_embeddings.npy', short=False)

  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 1/20, Loss: 6.5050


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 2/20, Loss: 5.5517


...

Epoch 18/20, Loss: 3.8851


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 19/20, Loss: 3.8369


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 20/20, Loss: 3.7944
lstm init validation perplexity xavier_normal: 207.88362006599726


In [15]:
class WeightDropLSTM(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, dropout=0.5, weight_dropout=0.5):
        super(WeightDropLSTM, self).__init__()
        self.weight_dropout = weight_dropout
        # Original LSTM without dropout on weights
        self.lstm = torch.nn.LSTM(input_size, hidden_size, num_layers, dropout=dropout)
        # Store the original weights
        self._setup_weight_drop()

        # Apply weight drop to hidden-to-hidden weights
        for name, param in self.lstm.named_parameters():
            if 'weight_hh' in name:
                self.register_parameter(name + '_raw', nn.Parameter(param.data))
                param.requires_grad = False

    def _setup_weight_drop(self):
        """Modify the LSTM weights to include dropout only on the recurrent weights."""
        # Iterate over LSTM parameters and find recurrent weights
        for name_w in ['weight_hh_l0', 'weight_hh_l0_reverse']:
            if hasattr(self.lstm, name_w):
                # Save original weights
                raw_w = getattr(self.lstm, name_w).data
                # Register original weight as a persistent buffer
                self.register_parameter(f'{name_w}_raw', nn.Parameter(raw_w))

                # Replace the original weight with the dropped version during training
                setattr(self.lstm, name_w, nn.Parameter(self._weight_drop(getattr(self, f'{name_w}_raw'))))

    def _weight_drop(self, weights):
        """Apply dropout to the recurrent weights during training."""
        if self.training:
            return F.dropout(weights, p=self.weight_dropout, training=True)
        else:
            return weights

    def forward(self, x, hidden=None):
        """Forward pass of the LSTM with weight drop on recurrent weights."""
        # Apply weight dropout
        self._setup_weight_drop()
        output, hidden = self.lstm(x, hidden)
        return output, hidden

class VariationalDropout(nn.Module):
    def __init__(self, dropout=0.5):
        super(VariationalDropout, self).__init__()
        self.dropout = dropout

    def forward(self, x):
        if not self.training or self.dropout == 0:
            return x

        mask = x.new_empty(x.size(0), 1, x.size(2)).bernoulli_(1 - self.dropout)
        mask = mask.div_(1 - self.dropout)
        return mask * x

class EmbeddingDropout(nn.Module):
    def __init__(self, embed, dropout=0.1):
        super(EmbeddingDropout, self).__init__()
        self.embed = embed
        self.dropout = dropout

    def forward(self, words):
        if not self.training or self.dropout == 0:
            return self.embed(words)

        mask = self.embed.weight.data.new().resize_((self.embed.weight.size(0), 1))
        mask.bernoulli_(1 - self.dropout)
        mask = mask.expand_as(self.embed.weight) / (1 - self.dropout)
        masked_embed_weight = mask * self.embed.weight

        padding_idx = self.embed.padding_idx
        if padding_idx is not None:
            masked_embed_weight[padding_idx] = 0

        return F.embedding(words, masked_embed_weight)

class RegularizedLSTM(nn.Module):
    def __init__(self, embed_dim: int = 128, n_layer: int = 3, hidden_dim: int = 512, dropout_rate: float = 0.5, embedding_type: str = "default", regularizations: List[str] = []):
        super(RegularizedLSTM, self).__init__()
        print("using regularized lstm")
        if "embedding_dropout" in regularizations:
          print("using embedding dropout")
          self.embedding = EmbeddingDropout(nn.Embedding(vocab.size(), embed_dim), dropout=0.1)
        else:
          self.embedding = nn.Embedding(vocab.size(), embed_dim)
        if "weight_drop_lstm" in regularizations:
          print("using weight drop")
          self.lstm = WeightDropLSTM(embed_dim, hidden_dim, n_layer, dropout=dropout_rate)
        else:
          self.lstm = nn.LSTM(embed_dim, hidden_dim, n_layer, dropout=dropout_rate)

        self.fc1 = torch.nn.Linear(hidden_dim, embed_dim)
        self.fc2 = torch.nn.Linear(embed_dim, vocab.size())

        # Tie weights
        if "embedding_dropout" in regularizations:
          self.fc2.weight = self.embedding.embed.weight
        else:
          self.fc2.weight = self.embedding.weight

    def forward(self, x, state: Optional[Tuple[torch.Tensor, torch.Tensor]]=None):
        emb = self.embedding(x)
        output, state = self.lstm(emb, state)
        #output = self.dropout(output)
        # Project down to embed_dim
        output = self.fc1(output)

        # Project to vocab_size
        logits = self.fc2(output)
        # Compute log probabilities
        log_probs = F.log_softmax(logits, dim=-1)
        return log_probs, state

In [36]:
from itertools import product

def optimize_parameters(param_grid = {
        'model_type': ['default'],
        'lr': [1e-2, 5e-3, 1e-3],
        'embed_dim': [128, 512],
        'n_layer': [3],
        'hidden_dim': [256, 1024], #[256, 512, 1024],
        'dropout_rate': [0.5] #[0.3, 0.5, 0.7]
    }):

    best_perplex = float('inf')
    best_params = {}
    best_model = None

    for params in product(*param_grid.values()):
        current_params = dict(zip(param_grid.keys(), params))
        #embed_dim: int = 128, n_layer: int = 3, hidden_dim: int = 512, dropout_rate: float = 0.5,
        model = LSTMModel(device="cuda", model=current_params["model_type"], embedding_type="default", embed_dim=current_params['embed_dim'], hidden_dim=current_params['hidden_dim'],n_layer=current_params['n_layer'], dropout_rate=current_params['dropout_rate'], regularizations=current_params['regularizations'])

        print(f"{current_params['model_type']} lstm for {model}, default, {current_params}")
        model.train(lr=current_params['lr'])
        val_perplex = model.dataset_perplexity(tok_validation_dataset)
        print(f"{current_params['model_type']} lstm validation perplexity for {model}, default, {current_params} = {val_perplex}")

        if val_perplex < best_perplex:
            best_perplex = val_perplex
            best_params = current_params
            best_model = model

    return best_params, best_model, best_perplex

def optimize_parameters_list(param_list = []):

    best_perplex = float('inf')
    best_params = {}
    best_model = None

    for current_params in param_list:
        #embed_dim: int = 128, n_layer: int = 3, hidden_dim: int = 512, dropout_rate: float = 0.5,
        model = LSTMModel(device="cuda", model=current_params["model_type"], embedding_type="default", embed_dim=current_params['embed_dim'], hidden_dim=current_params['hidden_dim'],n_layer=current_params['n_layer'], dropout_rate=current_params['dropout_rate'], regularizations=current_params['regularizations'])

        print(f"{current_params['model_type']} lstm for {model}, default, {current_params}")
        model.train(lr=current_params['lr'], patience=0)
        val_perplex = model.dataset_perplexity(tok_validation_dataset)
        print(f"{current_params['model_type']} lstm validation perplexity for {model}, default, {current_params} = {val_perplex}")

        if val_perplex < best_perplex:
            best_perplex = val_perplex
            best_params = current_params
            best_model = model

    return best_params, best_model, best_perplex

In [20]:
param_grid = {
        'model_type': ['default', 'regularized_full'],
        'lr': [1e-2, 5e-3, 1e-3],
        'embed_dim': [128, 512],
        'n_layer': [3],
        'hidden_dim': [256, 1024], #[256, 512, 1024],
        'dropout_rate': [0.5] #[0.3, 0.5, 0.7]
    }
for params in product(*param_grid.values()):
  current_params = dict(zip(param_grid.keys(), params))
  print(current_params)

{'model_type': 'default', 'lr': 0.01, 'embed_dim': 128, 'n_layer': 3, 'hidden_dim': 256, 'dropout_rate': 0.5}
{'model_type': 'default', 'lr': 0.01, 'embed_dim': 128, 'n_layer': 3, 'hidden_dim': 1024, 'dropout_rate': 0.5}
{'model_type': 'default', 'lr': 0.01, 'embed_dim': 512, 'n_layer': 3, 'hidden_dim': 256, 'dropout_rate': 0.5}
{'model_type': 'default', 'lr': 0.01, 'embed_dim': 512, 'n_layer': 3, 'hidden_dim': 1024, 'dropout_rate': 0.5}
{'model_type': 'default', 'lr': 0.005, 'embed_dim': 128, 'n_layer': 3, 'hidden_dim': 256, 'dropout_rate': 0.5}
{'model_type': 'default', 'lr': 0.005, 'embed_dim': 128, 'n_layer': 3, 'hidden_dim': 1024, 'dropout_rate': 0.5}
{'model_type': 'default', 'lr': 0.005, 'embed_dim': 512, 'n_layer': 3, 'hidden_dim': 256, 'dropout_rate': 0.5}
{'model_type': 'default', 'lr': 0.005, 'embed_dim': 512, 'n_layer': 3, 'hidden_dim': 1024, 'dropout_rate': 0.5}
{'model_type': 'default', 'lr': 0.001, 'embed_dim': 128, 'n_layer': 3, 'hidden_dim': 256, 'dropout_rate': 0.5}
{

Default model LR tuning with LambdaLR scheduler and Early Stopping


In [ ]:
param_grid = {
        'model_type': ['default'],
        'lr': [1e-3],
        'embed_dim': [128],
        'n_layer': [3],
        'hidden_dim': [256], #[256, 512, 1024],
        'dropout_rate': [0.3, 0.5, 0.7] #[0.3, 0.5, 0.7]
    }
best_params, best_model, best_perplex = optimize_parameters(param_grid=param_grid)
#save_truncated_distribution(best_model, 'lstm_predictions_embeddings_best_new_architecture.npy', short=False)

default lstm for <__main__.LSTMModel object at 0x780fa76267d0>, default, {'model_type': 'default', 'lr': 0.001, 'embed_dim': 128, 'n_layer': 3, 'hidden_dim': 256, 'dropout_rate': 0.3}


  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 1/20, Loss: 6.9956
lstm validation perplexity: 506.7920107710479
lstm validation loss: 6.228100684256131


  0%|          | 0/1014 [00:00<?, ?it/s]

...

Epoch 18/20, Loss: 5.0227
lstm validation perplexity: 198.1286601054691
lstm validation loss: 5.288916618179364


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 19/20, Loss: 4.9925
lstm validation perplexity: 196.3059531410905
lstm validation loss: 5.279674427572902


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 20/20, Loss: 4.9642
lstm validation perplexity: 192.58446957825652
lstm validation loss: 5.260534860485885
default lstm validation perplexity for <__main__.LSTMModel object at 0x780fe9c4e800>, default, {'model_type': 'default', 'lr': 0.001, 'embed_dim': 128, 'n_layer': 3, 'hidden_dim': 256, 'dropout_rate': 0.7} = 192.80501150811648


In [ ]:
param_grid = {
        'model_type': ['default'],
        'lr': [1e-3],
        'embed_dim': [256],
        'n_layer': [3],
        'hidden_dim': [512], #[256, 512, 1024],
        'dropout_rate': [0.1, 0.3, 0.5] #[0.3, 0.5, 0.7]
    }
best_params, best_model, best_perplex = optimize_parameters(param_grid=param_grid)
save_truncated_distribution(best_model, 'lstm_predictions_embeddings_best_new_architecture.npy', short=False)

default lstm for <__main__.LSTMModel object at 0x780fa72124d0>, default, {'model_type': 'default', 'lr': 0.001, 'embed_dim': 256, 'n_layer': 3, 'hidden_dim': 512, 'dropout_rate': 0.1}


  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 1/20, Loss: 6.6927
lstm validation perplexity: 390.9193368903453
lstm validation loss: 5.968501239189511


  0%|          | 0/1014 [00:00<?, ?it/s]

...

Epoch 10/20, Loss: 4.4796
lstm validation perplexity: 181.87480438991213
lstm validation loss: 5.203318562405795


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 11/20, Loss: 4.4039
lstm validation perplexity: 182.12248286793533
lstm validation loss: 5.204679443516278


  0%|          | 0/1014 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [ ]:
param_grid = {
        'model_type': ['default'],
        'lr': [1e-3, 1e-4],
        'embed_dim': [256],
        'n_layer': [3],
        'hidden_dim': [512], #[256, 512, 1024],
        'dropout_rate': [0.2] #[0.3, 0.5, 0.7]
    }
best_params, best_model, best_perplex = optimize_parameters(param_grid=param_grid)

default lstm for <__main__.LSTMModel object at 0x780fa719bac0>, default, {'model_type': 'default', 'lr': 0.001, 'embed_dim': 256, 'n_layer': 3, 'hidden_dim': 512, 'dropout_rate': 0.2}


  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 1/20, Loss: 6.7764
lstm validation perplexity: 414.380223226878
lstm validation loss: 6.026783965933089


  0%|          | 0/1014 [00:00<?, ?it/s]

...

Epoch 18/20, Loss: 5.4350
lstm validation perplexity: 279.8319603518558
lstm validation loss: 5.634189281411681


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 19/20, Loss: 5.3895
lstm validation perplexity: 277.32704485385244
lstm validation loss: 5.625197477090201


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 20/20, Loss: 5.3465
lstm validation perplexity: 273.86066155642084
lstm validation loss: 5.612619442574948
default lstm validation perplexity for <__main__.LSTMModel object at 0x780fa701ffd0>, default, {'model_type': 'default', 'lr': 0.0001, 'embed_dim': 256, 'n_layer': 3, 'hidden_dim': 512, 'dropout_rate': 0.2} = 274.0759952079062


In [ ]:
param_grid = {
        'model_type': ['default'],
        'lr': [1e-3],
        'embed_dim': [512],
        'n_layer': [3],
        'hidden_dim': [1024], #[256, 512, 1024],
        'dropout_rate': [0.1, 0.2, 0.3] #[0.3, 0.5, 0.7]
    }
best_params, best_model, best_perplex = optimize_parameters(param_grid=param_grid)

default lstm for <__main__.LSTMModel object at 0x780fe1529b70>, default, {'model_type': 'default', 'lr': 0.001, 'embed_dim': 512, 'n_layer': 3, 'hidden_dim': 1024, 'dropout_rate': 0.1}


  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 1/20, Loss: 6.5779
lstm validation perplexity: 340.1301239897592
lstm validation loss: 5.829328262009439


  0%|          | 0/1014 [00:00<?, ?it/s]

...

Epoch 6/20, Loss: 4.4625
lstm validation perplexity: 195.15572538435296
lstm validation loss: 5.273797831573679


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 7/20, Loss: 4.2846
lstm validation perplexity: 205.0275413436308
lstm validation loss: 5.323144318132233


  0%|          | 0/1014 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [13]:
param_grid = {
        'model_type': ['regularized_full'],
        'regularizations': [['embedding_dropout'], ['weight_drop_lstm'], ['embedding_dropout', 'weight_drop_lstm']],
        'lr': [1e-3],
        'embed_dim': [512],
        'n_layer': [3],
        'hidden_dim': [1024], #[256, 512, 1024],
        'dropout_rate': [0.5, 0.7, 0.9] #[0.3, 0.5, 0.7]
    }
best_params, best_model, best_perplex = optimize_parameters(param_grid=param_grid)

NameError: name 'RegularizedLSTM' is not defined

In [ ]:
param_grid = {'model_type': ['regularized_full'], 'regularizations': [['embedding_dropout'], ['weight_drop_lstm'], ['embedding_dropout', 'weight_drop_lstm']], 'lr': [1e-3], 'embed_dim': [512], 'n_layer': [3], 'hidden_dim': [2048], 'dropout_rate': [0.7, 0.9]}
best_params, best_model, best_perplex = optimize_parameters(param_grid=param_grid)
save_truncated_distribution(best_model, 'lstm_regularized_improved_predictions.npy')

using regularized lstm
regularized_full lstm for <__main__.LSTMModel object at 0x7d9ff14dba60>, default, {'model_type': 'regularized_full', 'regularizations': ['embedding_dropout'], 'lr': 0.001, 'embed_dim': 512, 'n_layer': 3, 'hidden_dim': 2048, 'dropout_rate': 0.7}


  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 1/20, Loss: 6.5541
lstm validation perplexity: 358.9448050084952
lstm validation loss: 5.883168630173633


  0%|          | 0/1014 [00:00<?, ?it/s]

...

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 3/20, Loss: 5.4799
lstm validation perplexity: 233.1849108583602
lstm validation loss: 5.451831747658884


  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 4/20, Loss: 5.2209
lstm validation perplexity: 203.4238717892357
lstm validation loss: 5.315291840490093


  0%|          | 0/1014 [00:00<?, ?it/s]

In [55]:
param_grid = {
    'model_type': ['regularized_full'],
    'regularizations': [['embedding_dropout'], ['weight_drop_lstm'], ['embedding_dropout', 'weight_drop_lstm']],
    'lr': [1e-3],
    'embed_dim': [256],
    'n_layer': [3],
    'hidden_dim': [1024],
    'dropout_rate': [0.3, 0.5, 0.7]
}
param_list = [
    {
        'model_type': 'regularized_full',
        'regularizations': ['embedding_dropout'],
        'lr': 1e-3,
        'embed_dim': 512,
        'n_layer': 3,
        'hidden_dim': 2048,
        'dropout_rate': 0.7,
    },
    {
        'model_type': 'regularized_full',
        'regularizations': ['weight_drop_lstm'],
        'lr': 1e-3,
        'embed_dim': 512,
        'n_layer': 3,
        'hidden_dim': 2048,
        'dropout_rate': 0.7,
    },
    {
        'model_type': 'regularized_full',
        'regularizations': ['embedding_dropout', 'weight_drop_lstm'],
        'lr': 1e-3,
        'embed_dim': 512,
        'n_layer': 3,
        'hidden_dim': 2048,
        'dropout_rate': 0.7,
    }
]
optimize_parameters(param_grid=param_grid)

using regularized lstm
using embedding dropout
regularized_full lstm for <__main__.LSTMModel object at 0x7edfcc8e9090>, default, {'model_type': 'regularized_full', 'regularizations': ['embedding_dropout'], 'lr': 0.001, 'embed_dim': 256, 'n_layer': 3, 'hidden_dim': 1024, 'dropout_rate': 0.3}


  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 1/20, Loss: 6.8819
lstm validation perplexity: 470.7972051488268
lstm validation loss: 6.154427438981132


  0%|          | 0/5000 [00:00<?, ?it/s]

...

  0%|          | 0/1014 [00:00<?, ?it/s]

Epoch 20/20, Loss: 4.7708
lstm validation perplexity: 188.17727425362833
lstm validation loss: 5.23738446669121


  0%|          | 0/5000 [00:00<?, ?it/s]

saved lstm_regularized_full_embedding_dropout-weight_drop_lstm_predictions_updated_{'embedding_type': 'default', 'embed_dim': 256, 'hidden_dim': 1024, 'n_layer': 3, 'dropout_rate': 0.7, 'regularizations': ['embedding_dropout', 'weight_drop_lstm']}.npy
regularized_full lstm validation perplexity for <__main__.LSTMModel object at 0x7edfcb707eb0>, default, {'model_type': 'regularized_full', 'regularizations': ['embedding_dropout', 'weight_drop_lstm'], 'lr': 0.001, 'embed_dim': 256, 'n_layer': 3, 'hidden_dim': 1024, 'dropout_rate': 0.7} = 188.97226982517134


({'model_type': 'regularized_full',
  'regularizations': ['weight_drop_lstm'],
  'lr': 0.001,
  'embed_dim': 256,
  'n_layer': 3,
  'hidden_dim': 1024,
  'dropout_rate': 0.5},
 154.09701545185945)

### Submission

Upload a submission with the following files to Gradescope:
* proj_1.ipynb (rename to match this exactly)
* lstm_predictions.npy (this should also include all improvements from your exploration)
* neural_trigram_predictions.npy
* bigram_predictions.npy
* report.pdf

You can upload files individually or as part of a zip file, but if using a zip file be sure you are zipping the files directly and not a folder that contains them.

Be sure to check the output of the autograder after it runs.  It should confirm that no files are missing and that the output files have the correct format.  Note that the test set perplexities shown by the autograder are on a completely different scale from your validation set perplexities due to truncating the distribution and selecting different text.  Don't worry if the values seem much worse.